This notebook processes a JSON file of N items into chunks of 1000 items. The items are stored as a JSON + Safetensor pair. The name of the safestensor file is written within the JSON file at index 1

In [1]:

import json
import pandas as pd
import os
import shelve
import torch
from safetensors.torch import save_file
import json

# Determine if this notebook is running on Colab or Kaggle
#Use https://www.kaggle.com/ if Google Colab GPU is busy
home_directory = '/content/'
using_Kaggle = os.environ.get('KAGGLE_URL_BASE','')
if using_Kaggle : home_directory = '/kaggle/working/'
%cd {home_directory}
#-------#
# Load the data if not already loaded
try:
    loaded
except:
    %cd {home_directory}
    !git clone https://huggingface.co/datasets/codeShare/text-to-image-prompts
    loaded = True
#--------#

/kaggle/working
/kaggle/working
Cloning into 'text-to-image-prompts'...
remote: Enumerating objects: 14733, done.
remote: Counting objects: 100% (14733/14733), done.
remote: Compressing objects: 100% (12461/12461), done.
remote: Total 14733 (delta 2198), reused 14108 (delta 2172), pack-reused 0 (from 0)
Receiving objects: 100% (14733/14733), 160.80 MiB | 23.51 MiB/s, done.
Resolving deltas: 100% (2198/2198), done.
Updating files: 100% (4962/4962), done.
Filtering content: 100% (1714/1714), 5.02 GiB | 106.60 MiB/s, done.


In [2]:
# @title Make your own text_encodings .safetensor file for later use (using GPU is recommended to speed things up)

# User input
target = home_directory + 'text-to-image-prompts/fanfic/tags/'
output_folder = home_directory + 'output/fanfic/tags/'
root_filename = 'fanfic_tags'
NUM_FILES = 1
#--------#

# Setup environment
def my_mkdirs(folder):
    if os.path.exists(folder)==False:
        os.makedirs(folder)
#--------#
output_folder_text = output_folder + 'text/'
output_folder_text = output_folder + 'text/'
output_folder_text_encodings = output_folder + 'text_encodings/'
target_raw = target + 'raw/'
%cd {home_directory}
my_mkdirs(output_folder)
my_mkdirs(output_folder_text)
my_mkdirs(output_folder_text_encodings)
#-------#

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("openai/clip-vit-large-patch14", clean_up_tokenization_spaces = False)
from transformers import  CLIPProcessor, CLIPModel
processor = CLIPProcessor.from_pretrained("openai/clip-vit-large-patch14" , clean_up_tokenization_spaces = True)
model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14").to(device)



%cd {target_raw}

filename = 'fanfic_tags.json'
with open(f'{root_filename}.json', 'r') as f:
  data = json.load(f)
#------#
_df = pd.DataFrame({'count': data})['count']
prompts = {
    key : value for key, value in _df.items()
}


# Quick fix
index = 0
_prompts = {}
for key in  prompts:
  if type(prompts[key]) != type(''):continue
  _prompts[f'{index}'] = prompts[key]
  index = index +1
#---------#
index = 0
prompts = {}
for key in _prompts:
  prompts[f'{index}'] = _prompts[key]
  index = index +1
#-----#

/kaggle/working


tokenizer_config.json:   0%|          | 0.00/905 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/961k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/525k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.22M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/389 [00:00<?, ?B/s]

preprocessor_config.json:   0%|          | 0.00/316 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/4.52k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.71G [00:00<?, ?B/s]

/kaggle/working/text-to-image-prompts/fanfic/tags/raw


In [ ]:

#---------#
for  file_index in range(NUM_FILES + 1):
    if (file_index < 1): continue
    filename = f'{root_filename}-{file_index}'
    if (NUM_FILES == 1) : filename = f'{root_filename}'
    for key in prompts:
      index = index + 1
    #----------#
    NUM_ITEMS = index
    #------#

  # Calculate text_encoding for .json file contents and results as .db file
    names_dict = {}
    text_encoding_dict = {}
    segments = {}
    index = 0;
    _subby = 1;
    NUM_HEADERS = 2
    CHUNKS_SIZE = 1000
    _filename = ''
    subby_offset = 256
    subby = _subby + subby_offset
    offset = subby_offset*998
    for __index in range(NUM_ITEMS-offset):
        _index = __index + offset
        if (index % 100 == 0) : print(index)
        if (index == 0 and _index>0) : index = index + 2 #make space for headers
        if (_index % (CHUNKS_SIZE-NUM_HEADERS) == 0 and _index > 0) :

            # Write headers in the .json
            names_dict[f'{0}'] = f'{_index}'
            names_dict[f'{1}'] = f'{filename}-{subby}'

            # Encode the headers into text_encoding
            inputs = tokenizer(text = '' + names_dict[f'{0}'], padding=True, return_tensors="pt").to(device)
            text_features = model.get_text_features(**inputs).to(device)
            text_features =  text_features/text_features.norm(p=2, dim=-1, keepdim=True)
            text_encoding_dict[f'{0}'] = text_features.to(torch.device('cpu'))
            inputs = tokenizer(text = '' + names_dict[f'{1}'], padding=True, return_tensors="pt").to(device)
            text_features = model.get_text_features(**inputs).to(device)
            text_features =  text_features/text_features.norm(p=2, dim=-1, keepdim=True)
            text_encoding_dict[f'{1}'] = text_features.to(torch.device('cpu'))
            #-------#

            # Write .json
            _filename = f'{filename}-{subby}.json'
            %cd {output_folder_text}
            print(f'Saving segment {_filename} to {output_folder_text}...')
            with open(_filename, 'w') as f:
                json.dump(names_dict, f)
            #-------#

            # Write .safetensors
            _filename = f'{filename}-{subby}.safetensors'
            %cd {output_folder_text_encodings}
            print(f'Saving segment {_filename} to {output_folder_text_encodings}...')
            save_file(text_encoding_dict, _filename)
            #--------#

            #Iterate
            subby = subby + 1
            segments[f'{subby}'] = _filename
            text_encoding_dict = {}
            names_dict = {}
            index = 0
            #------#
            #------#
        else: index = index + 1
        #--------#
        inputs = tokenizer(text = '' + prompts[f'{_index}'], padding=True, return_tensors="pt").to(device)
        text_features = model.get_text_features(**inputs).to(device)
        text_features =  text_features/text_features.norm(p=2, dim=-1, keepdim=True)
        text_encoding_dict[f'{index}'] = text_features.to(torch.device('cpu'))
        names_dict[f'{index}'] = prompts[f'{_index}']
        continue
    #-----#
    #-----#
    # Write headers in the .json
    names_dict[f'{0}'] = f'{_index}'
    names_dict[f'{1}'] = f'{filename}-{subby}'

    # Encode the headers into text_encoding
    inputs = tokenizer(text = '' + names_dict[f'{0}'], padding=True, return_tensors="pt").to(device)
    text_features = model.get_text_features(**inputs).to(device)
    text_features =  text_features/text_features.norm(p=2, dim=-1, keepdim=True)
    text_encoding_dict[f'{0}'] = text_features.to(torch.device('cpu'))
    inputs = tokenizer(text = '' + names_dict[f'{1}'], padding=True, return_tensors="pt").to(device)
    text_features = model.get_text_features(**inputs).to(device)
    text_features =  text_features/text_features.norm(p=2, dim=-1, keepdim=True)
    text_encoding_dict[f'{1}'] = text_features.to(torch.device('cpu'))
    #-------#

    # Write .json
    _filename = f'{filename}-{subby}.json'
    %cd {output_folder_text}
    print(f'Saving segment {_filename} to {output_folder_text}...')
    with open(_filename, 'w') as f:
        json.dump(names_dict, f)
    #-------#

    # Write .safetensors
    _filename = f'{filename}-{subby}.safetensors'
    %cd {output_folder_text_encodings}
    print(f'Saving segment {_filename} to {output_folder_text_encodings}...')
    save_file(text_encoding_dict, _filename)
    #--------#

    #Iterate
    subby = subby + 1
    segments[f'{subby}'] = _filename
    text_encoding_dict = {}
    names_dict = {}
    index = 0
    #------#
  #----#

0
/kaggle/working/output/fanfic/tags/text
Saving segment fanfic_tags-257.json to /kaggle/working/output/fanfic/tags/text/...
/kaggle/working/output/fanfic/tags/text_encodings
Saving segment fanfic_tags-257.safetensors to /kaggle/working/output/fanfic/tags/text_encodings/...
0
100
200
300
400
500
600
700
800
900
/kaggle/working/output/fanfic/tags/text
Saving segment fanfic_tags-258.json to /kaggle/working/output/fanfic/tags/text/...
/kaggle/working/output/fanfic/tags/text_encodings
Saving segment fanfic_tags-258.safetensors to /kaggle/working/output/fanfic/tags/text_encodings/...
0
100
200
300
400
500
600
700
800
900
/kaggle/working/output/fanfic/tags/text
Saving segment fanfic_tags-259.json to /kaggle/working/output/fanfic/tags/text/...
/kaggle/working/output/fanfic/tags/text_encodings
Saving segment fanfic_tags-259.safetensors to /kaggle/working/output/fanfic/tags/text_encodings/...
0
100
200
300
400
500
600
700
800
900
/kaggle/working/output/fanfic/tags/text
Saving segment fanfic_tag

In [11]:
# @title Download the text_encodings as .zip
# UP TO FILE INDEX 250 FOR fanfic tags out of a total 1622
import os
%cd {home_directory}
output_folder = '/content/output'
#os.remove(f'{home_directory}results.zip')
zip_dest = f'{home_directory}results.zip'
!zip -r {zip_dest} '/content/output'

/content

  adding: content/output/ (stored 0%)

  adding: content/output/fanfic/ (stored 0%)

  adding: content/output/fanfic/tags/ (stored 0%)

  adding: content/output/fanfic/tags/text_encodings/ (stored 0%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-28.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-103.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-218.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-123.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-167.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-180.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-58.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-201.safetensors (deflated 9%)

  adding: content/output/fanfi

In [14]:
# @title Download the text_encodings to google drive as .zip
from google.colab import drive

output_folder = '/content/output'
#-----#
try: mounted
except:
  mounted = True
  drive.mount('/content/drive')
#------#


Mounted at /content/drive


In [15]:

zip_dest = '/content/drive/MyDrive/fanfic1.zip'
!zip -r {zip_dest} {output_folder}

  adding: content/output/ (stored 0%)

  adding: content/output/fanfic/ (stored 0%)

  adding: content/output/fanfic/tags/ (stored 0%)

  adding: content/output/fanfic/tags/text_encodings/ (stored 0%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-28.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-103.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-218.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-123.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-167.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-180.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-58.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/text_encodings/fanfic_tags-201.safetensors (deflated 9%)

  adding: content/output/fanfic/tags/tex